#✅ GAN 모델 생성하기
**GAN**은 딥러닝의 원리를 활용해 가상 이미지를 생성하는 알고리즘입니다.

GAN에는 생성자, 판별자가 있으며, 적대적 신경망을 통해 만들어낸 이미지를 판별합니다.

실습을 통해 GAN 모델을 직접 생성해봅시다!


*(노트북 과부하 염려가 있어 코드 작성까지만 해주시면 됩니다)*


In [1]:
#라이브러리
from tensorflow.keras.datasets import mnist
from tensorflow.keras.layers import Input, Dense, Reshape, Flatten, Dropout
from tensorflow.keras.layers import BatchNormalization, Activation, LeakyReLU, UpSampling2D, Conv2D
from tensorflow.keras.models import Sequential, Model

import numpy as np
import matplotlib.pyplot as plt

In [7]:
#생성자 모델 만들기
generator = Sequential()
generator.add(Dense(128*7*7,input_dim = 100, activation = LeakyReLU(0.2)))
generator.add(BatchNormalization())
generator.add(Reshape((7,7,128)))
generator.add(UpSampling2D())
generator.add(Conv2D(64,kernel_size=5,padding='same'))
generator.add(BatchNormalization())
generator.add(Activation(LeakyReLU(0.2)))
generator.add(UpSampling2D())
generator.add(Conv2D(1, kernel_size=5,padding='same',activation='tanh'))

In [15]:
#판별자 모델 만들기
discriminator = Sequential()
discriminator.add(Conv2D(64,kernel_size=5, strides=2, input_shape=(28,28,1),padding="same"))
discriminator.add(Activation(LeakyReLU(0.2)))
discriminator.add(Dropout(0.3))
discriminator.add(Conv2D(128,kernel_size=5,strides=2,padding="same"))
discriminator.add(Activation(LeakyReLU(0.2)))
discriminator.add(Dropout(0.3))
discriminator.add(Flatten())
discriminator.add(Dense(1,activation='sigmoid'))
discriminator.compile(loss='binary_crossentropy',optimizer='adam')
discriminator.trainable=False

In [21]:
#생성자와 판별자 모델을 연결시키는 gan 모델 만들기
ginput = Input(shape=(100,))
dis_output = discriminator(generator(ginput))
gan = Model(ginput, dis_output)
gan.compile(loss='binary_crossentropy',optimizer='adam')

In [34]:
#신경망을 실행시키는 함수 만들기

def gan_train(epochs, batch_size, saving_interval):

  (X_train,_),(_,_) = mnist.load_data()
  X_train = X_train.reshape(X_train.shape[0],28,28,1).astype('float32')

  X_train = (X_train - 127.5) / 127.5

  true = np.ones((batch_size,1))
  fake = np.zeros((batch_size,1))

  for i in range(epochs):
    #실제 데이터를 판별자에 입력
    idx = np.random.randint(0, X_train.shape[0], batch_size)
    real_imgs = X_train[idx]


    #가상 이미지를 판별자에 입력
    noise = np.random.normal(0, 1, (batch_size, 100))
    gen_imgs = generator.predict(noise)
    d_loss_fake = discriminator.train_on_batch(gen_imgs, fake)

    #판별자와 생성자의 오차 계산
    d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)

    print('epoch: %d' % i, 'd_loss: %.4f' % d_loss, 'g_loss: %.4f' % g_loss)

    #중간 과정을 이미지로 저장하는 부분
    if i % saving_interval == 0:
      noise = np.random.normal(0,1,(25,100))
      gen_imgs = 0.5 * gen_imgs + 0.5

      fig, axs = plt.subplots(5,5)
      count = 0
      for j in range(5):
        for k in range(5):
          axs[j,k].imshow(gen_imgs[count,:,:,0], cmap='gray')
          axs[j,k].axis('off')
          count += 1
      fig.savefig("gan_images/gan_mnist_%d.png"%i)

#gan_train(2001,32,200)



#🔍 전이 학습
기존 모델의 가중치를 가져와 생성할 모델에 활용하는 것을 **전이 학습**이라고 합니다.

모델을 불러오고, 모델의 설정하는 과정에서 빠진 부분을 채워봅시다!

In [67]:
#라이브러리
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras import Input, models, layers, optimizers, metrics
from tensorflow.keras.layers import Dense, Flatten, Activation, Dropout
from tensorflow.keras.applications import VGG16
from tensorflow.keras.callbacks import EarlyStopping

In [68]:
#데이터 가져오기
!git clone https://github.com/taehojo/data-ch20.git

fatal: destination path 'data-ch20' already exists and is not an empty directory.


In [69]:
#학습셋 변형 설정
train_datagen = ImageDataGenerator(rescale = 1./255,
                                   horizontal_flip =True,
                                   width_shift_range=0.1,
                                   height_shift_range=0.1)

train_generator = train_datagen.flow_from_directory(
    './data-ch20/train',
    target_size=(150,150),
    batch_size=5,
    class_mode = 'binary'
)

#테스트셋의 정규화 설정
test_datagen = ImageDataGenerator(rescale=1./255)

test_generator = test_datagen.flow_from_directory(
    './data-ch20/test',
    target_size=(150,150),
    batch_size=5,
    class_mode='binary'
)

Found 160 images belonging to 2 classes.
Found 120 images belonging to 2 classes.


In [70]:
#VGG16 모델 불러오기
transfer_model = VGG16(weights='imagenet', include_top=False, input_shape=(150,150,3))
transfer_model.trainable = False

In [71]:
#모델 설정하기
finetune_model = models.Sequential()
finetune_model.add(transfer_model)
finetune_model.add(Flatten())
finetune_model.add(Dense(64))
finetune_model.add(Activation('relu'))
finetune_model.add(Dropout(0.5))
finetune_model.add(Dense(1))
finetune_model.add(Activation('sigmoid'))

In [74]:
from keras import optimizers
from keras.callbacks import EarlyStopping

#모델 실행 옵션 설정
finetune_model.compile(loss='binary_crossentropy', optimizer=optimizers.Adam(), metrics=['accuracy'])

#학습의 조기 중단 설정
early_stopping_callback = EarlyStopping(monitor='val_loss', patience=5)

#모델 실행
history = finetune_model.fit(train_generator,epochs=20,validation_data=test_generator,
validation_steps=10,callbacks=[early_stopping_callback])

#검증셋과 학습셋의 오차 저장
y_vloss = history.history['val_loss']
y_loss = history.history['loss']

Epoch 1/20
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - accuracy: 0.5057 - loss: 0.8769

/usr/local/lib/python3.11/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


32/32 ━━━━━━━━━━━━━━━━━━━━ 54s 2s/step - accuracy: 0.5078 - loss: 0.8740 - val_accuracy: 0.7600 - val_loss: 0.5189
Epoch 2/20
32/32 ━━━━━━━━━━━━━━━━━━━━ 82s 3s/step - accuracy: 0.6956 - loss: 0.5584 - val_accuracy: 0.8800 - val_loss: 0.3695
Epoch 3/20
32/32 ━━━━━━━━━━━━━━━━━━━━ 52s 2s/step - accuracy: 0.7729 - loss: 0.4354 - val_accuracy: 0.8600 - val_loss: 0.3928
Epoch 4/20
32/32 ━━━━━━━━━━━━━━━━━━━━ 52s 2s/step - accuracy: 0.8707 - loss: 0.3568 - val_accuracy: 0.9400 - val_loss: 0.2394
Epoch 5/20
32/32 ━━━━━━━━━━━━━━━━━━━━ 0s 1s/step - accuracy: 0.7515 - loss: 0.4081

KeyboardInterrupt: 

In [ ]:
#그래프로 표현하기
x_len = np.arange(len(y_loss))
plt.plot(x_len, y_vloss, marker='.',c='red', label='Testset_loss')
plt.plot(x_len, y_loss, marker='.',c='blue',label='Trainset_loss')

plt.legend(loc='upper right')
plt.grid()
plt.xlabel('epoch')
plt.ylabel('loss')
plt.show